#  Focal Loss

Focal Loss — это функция потерь, используемая в нейронных сетях для решения проблемы классификации *сложных* объектов (hard examples).

**Приведем пример:** пусть модель должна классифицировать фрукты на два класса: яблоки и груши. В наборе данных есть много явных представителей того и иного класса: зеленые яблоки и желтые груши. Для модели они будут *простыми*: она на них не ошибается, и предсказываемая вероятность истинного класса для них велика и равна $0.9$.

В то же время в наборе данных есть малое количество зеленых груш: они по форме похожи на груши, а по цвету — на яблоки. Говоря более общими словами, зеленые груши *ближе к границе классов в пространстве признаков*. Для модели такие примеры могут оказаться *сложными*, и она будет на них ошибаться. Пусть для зеленой груши вероятность истинного класса равна $0.2$, то есть модель ошиблась и предсказала класс "яблоко" с вероятностью $0.8$.

<img src='https://edunet.kea.su/repo/EduNet-additions/FL/hard_examples_fruits.png' width=800></img>

Проблема состоит в том, что сумма большого количества малых ошибок на *простых* объектах может перевешивать сумму малого количества больших ошибок на *сложных* объектах. Поэтому модель будет плохо учиться верно классифицировать сложные объекты: ей будет "лень" исправлять незначительные ошибки.

Для решения этой проблемы была предложена специальная функция потерь — Focal Loss. Она немного модифицирует кросс-энтропию для придания большей значимости ошибкам на сложных объектах.

Focal Loss была предложена в статье [Focal Loss for Dense Object Detection (Lin et al., 2017)](https://arxiv.org/abs/1708.02002) изначально для задачи детектирования объектов на изображениях. Она определяется так:

$$\large\text{FL}(p_t) = -(1 - p_t)^\gamma\text{log}(p_t)$$

Здесь $p_t$ — предсказанная вероятность истинного класса, а $\gamma$ — настраиваемый гиперпараметр.

Focal Loss уменьшает потери на уверенно классифицируемых примерах (где $p_t>0.5$) и больше фокусируется на сложных примерах, которые классифицированы неправильно. Параметр $\gamma$ управляет относительной важностью неправильно классифицируемых примеров. Более высокое значение $\gamma$ увеличивает важность неправильно классифицированных примеров. В экспериментах авторы показали, что параметр $\gamma=2$ показывал себя наилучшим образом в их задаче.

При $\gamma=0$ Focal Loss становится равной Cross-Entropy Loss, которая выражается как обратный логарифм вероятности истинного класса:

$$\large\text{CE}(p_t)=-\text{log}(p_t)$$

**Разберем на нашем примере** с яблоками и грушами.

Мы имеем **20 простых** объектов с вероятностью истинного класса $0.9$: 10 яблок и 10 груш, **и один сложный** объект с вероятностью истинного класса $0.2$.


$\large{\text{CE} = \overbrace{\sum^{20}-\text{log}(0.9)}^{\large\color{#3C8031}{\text{loss(easy apples and pears)=2.11}}} + \overbrace{(-\text{log}(0.2))}^{\large\color{#F26035}{\text{loss(hard pear)=1.61}}} \approx 3.72}$

$\large{\text{FL}(\gamma=2) = \overbrace{\sum^{20}-\color{#AF3235}{\underbrace{(1-0.9)^2}_{0.01}}\text{log}(0.9)}^{\large\color{#3C8031}{\text{loss(easy apples and pears)=0.02}}} + \overbrace{(-\color{#AF3235}{\underbrace{(1-0.2)^2}_{0.64}}\text{log}(0.2))}^{\large\color{#F26035}{\text{loss(hard pear)=1.03}}} \approx 1.05}$

Фактически, потери для уверенно классифицированных объектов дополнительно занижаются.

Этот эффект достигается путем домножения на коэффициент: $ \large(1-p_{t})^\gamma$

Пока модель ошибается, $p_{t}$ — мала, и значение выражения в скобках соответственно близко к 1.

Когда модель обучилась, значение $p_{t}$ становится близким к 1, а разность в скобках становится маленьким числом, которое возводится в степень $ \gamma \ge 0 $. Таким образом, домножение на это небольшое число нивелирует вклад верно классифицированных объектов.

Это позволяет модели сосредоточиться (сфокусироваться, отсюда и название) на изучении сложных объектов (hard examples).





В примере коэффициент $(1-p_t)^\gamma$ в Focal Loss в 100 раз занизил потери при уверенной классификации простых яблок и груш, и потери при неверной классификации сложной груши стали преобладать.

<center><img src ="https://edunet.kea.su/repo/EduNet-additions/FL/focal_loss_vs_ce.png" width="700"></center>

<center><em>Source: <a href="https://arxiv.org/abs/1708.02002">Focal Loss for Dense Object Detection (Lin et al., 2018)</a></em></center>



Давайте посчитаем для различных значений $γ$, сколько понадобится примеров с небольшой ошибкой (высокой вероятностью истинного класса, равной $0.9$), чтобы получить суммарный **Focal Loss** примерно такой же, как у одного примера с большой ошибкой (низкой вероятностью истинного класса, равной $0.2$).

In [ ]:
import numpy as np

def cross_entropy(prob_true):
    return -np.log(prob_true)


def focal_loss(prob_true, gamma=2):
    return (1 - prob_true) ** gamma * cross_entropy(prob_true)


p1 = 0.9  # probability of easy examples predictions
p2 = 0.2  # probability of hard examples predictions
gammas = [0, 0.5, 1, 2, 5, 10, 15]

print(
    f"For probability of easy examples predictions {p1} and probability of hard examples predictions {p2}\n"
)

for gamma in gammas:
    fl1 = focal_loss(p1, gamma)
    fl2 = focal_loss(p2, gamma)

    print(
        f"gamma = {gamma},".ljust(15),
        f"for an equal loss with a problematic prediction, almost correct ones are required {int(fl2 / fl1)}",
    )

For probability of easy examples predictions 0.9 and probability of hard examples predictions 0.2

gamma = 0,      for an equal loss with a problematic prediction, almost correct ones are required 15
gamma = 0.5,    for an equal loss with a problematic prediction, almost correct ones are required 43
gamma = 1,      for an equal loss with a problematic prediction, almost correct ones are required 122
gamma = 2,      for an equal loss with a problematic prediction, almost correct ones are required 977
gamma = 5,      for an equal loss with a problematic prediction, almost correct ones are required 500548
gamma = 10,     for an equal loss with a problematic prediction, almost correct ones are required 16401977428
gamma = 15,     for an equal loss with a problematic prediction, almost correct ones are required 537459996388583


Как видно, при увеличении значения $\gamma$ можно достичь значительного роста "важности" примеров с высокой ошибкой, что по сути позволяет модели обращать внимание на "hard examples".

Этот пример также показывает **опасность Focal Loss**: если мы имеем **ошибки в разметке**, то при большом $\gamma$ можно начать очень сильно наказывать модель за ошибки на неверно размеченных примерах, что может привести к переобучению под ошибки в разметке.

Focal Loss может применяться также и в задачах с дисбалансом классов. В этом смысле объекты преобладающего класса могут считаться простыми, а объекты минорного класса — сложными.

Однако для работы с дисбалансом в Focal Loss могут быть добавлены веса для классов. Тогда формула будет выглядеть так:

$$\large\text{FL}(p_t) = -\alpha_t(1 - p_t)^\gamma\text{log}(p_t)$$

Здесь $\alpha_t$ — вес для истинного класса, имеющий такой же смысл, как параметр `weight` в Cross-Entropy Loss.

Focal Loss не реализована в PyTorch нативно, но существуют сторонние совместимые реализации. Посмотрим, как воспользоваться [одной из них](https://github.com/AdeelH/pytorch-multi-class-focal-loss).

In [ ]:
#!wget -qN https://raw.githubusercontent.com/AdeelH/pytorch-multi-class-focal-loss/master/focal_loss.py
!wget -qN https://edunet.kea.su/repo/EduNet-web_dependencies/dev-2.0/L05/focal_loss.py

In [ ]:
import torch
from focal_loss import FocalLoss


criterion = FocalLoss(alpha=None, gamma=2.)

model_output = torch.tensor([[2.4, 1.9, 7.3],
                             [9.5, 2.7, 4.0],
                             [5.7, 4.1, 0.2]])  # model output is logits, as in CrossEntropyLoss
print(f"model_output:\n {model_output}")

target = torch.tensor([2, 0, 1], dtype=torch.long)  # class labels
print(f"target: {target}")

loss_fl = criterion(model_output, target)
print(f"loss_fl: {loss_fl}")

model_output:
 tensor([[2.4000, 1.9000, 7.3000],
        [9.5000, 2.7000, 4.0000],
        [5.7000, 4.1000, 0.2000]])
target: tensor([2, 0, 1])
loss_fl: 0.4129861891269684


Убедимся, что сторонняя реализация вычисляет то, что нужно, и вычислим значение вручную. В первую очередь нужно перевести `model_output` из логитов в вероятности с помощью softmax.

In [ ]:
probs = torch.nn.functional.softmax(model_output, dim=1)

print(f"probabilities after softmax:\n {probs}")

probabilities after softmax:
 tensor([[0.0074, 0.0045, 0.9882],
        [0.9948, 0.0011, 0.0041],
        [0.8292, 0.1674, 0.0034]])


Теперь вручную рассчитаем значение функции потерь.

In [ ]:
def focal_loss(prob_true, gamma=2):
    return - (1 - prob_true) ** gamma * np.log(prob_true)

hand_calculated_loss = 0

for i in range(3):
    hand_calculated_loss += focal_loss(probs[i, target[i]])

hand_calculated_loss /= 3  # average by number of samples

print(f"hand-calculated focal loss:    {hand_calculated_loss.item()}")
print(f"library-calculated focal loss: {loss_fl}")
print(f"Are results almost equal? {torch.isclose(loss_fl, hand_calculated_loss).item()}")

hand-calculated focal loss:    0.4129861891269684
library-calculated focal loss: 0.4129861891269684
Are results almost equal? True


Действительно, при расчете вручную получили то же значение, что и при расчете с помощью сторонней реализации.

Мы рассмотрели Focal Loss — функцию потерь для классификации, используемую в нейронных сетях для решения проблемы классификации *сложных* объектов (hard examples), и получили интуицию того, как она позволяет придать большее значение ошибкам на объектах, которые модель классифицирует неуверенно.

# Дополнительные материалы

[Focal Loss for Dense Object Detection (Lin et al., 2018)](https://arxiv.org/abs/1708.02002)

[Understanding Focal Loss — A Quick Read](https://medium.com/visionwizard/understanding-focal-loss-a-quick-read-b914422913e7)